# Homework 1 (Total Points: 175)



Learning Goals:
- Learn how to load a dataset and process it.
- Learn how to implement several IR methods (TFIDF, BM25, QL) and understand their weaknesses & strengths.
- Learn how to evaluate IR methods


**NOTE 1**: Only the code (`TODO: Implement this!` denotes these sections) is graded. The 'theory' questions in this assignment serve as a preparation for the exam and to facilitate a deeper understanding of the course content. These questions (denoted by `TODO: Answer this!`) have no points assigned to them, but **need** to be filled out before submission.  

**NOTE 2**: You can use the `nltk`, `numpy` and `matplotlib` libraries here. Other libraries, e.g., `gensim` or `scikit-learn`, may not be used. 

**NOTE 3**: The notebook you submit has to have the student ids, seperated by underscores (E.g., `12341234_12341234_12341234.ipynb`). 

**NOTE 4**: Make sure to check that your notebook runs before submission. A quick way to do this is to restart the kernel and run all the cells.  

---
Additional Resources: 
-  Sections 2.3, 4.1, 4.2, 4.3, 5.3, 5.6, 5.7, 6.2, 7, 8 of [Search Engines: Information Retrieval in Practice](https://ciir.cs.umass.edu/downloads/SEIRiP.pdf)


In [1]:
# imports 
# TODO: Ensure that no additional library is imported in the notebook. 
# TODO: Only the standard library and the following libraries are allowed:

import os
import zipfile
from functools import partial

import nltk
import requests
import numpy as np
from tqdm import tqdm

import matplotlib.pyplot as plt

from ipywidgets import widgets
from IPython.display import display, HTML
from IPython.html import widgets
from collections import namedtuple

%matplotlib inline


/Users/catlinbruys/anaconda/lib/python3.6/site-packages/IPython/html.py:14: ShimWarning: The `IPython.html` package has been deprecated since IPython 4.0. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


## Section 1: Text Processing (20 points)

In this section, we will load the dataset and learn how to clean up the data to make it usable for an IR system. 

We are using the [CACM dataset](http://ir.dcs.gla.ac.uk/resources/test_collections/cacm/), which is a small, classic IR dataset, composed of a collection of titles and abstracts from the journal CACM. It comes with relevance judgements for queries, so we can evaluate our IR system. 

The following cell downloads the dataset and unzips it to a local directory

In [2]:
def download_dataset(folder_path = "./datasets/"):
    
    os.makedirs(folder_path, exist_ok=True)
    
    file_location = os.path.join(folder_path, "cacm.zip")
    
    # download file if it doesn't exist
    if not os.path.exists(file_location):
        
        url = "https://surfdrive.surf.nl/files/index.php/s/M0FGJpX2p8wDwxR/download"

        with open(file_location, "wb") as handle:
            print(f"Downloading file from {url} to {file_location}")
            response = requests.get(url, stream=True)
            for data in tqdm(response.iter_content()):
                handle.write(data)
            print("Finished downloading file")
    
    if not os.path.exists(os.path.join(folder_path, "train.txt")):
        
        # unzip file
        with zipfile.ZipFile(file_location, 'r') as zip_ref:
            zip_ref.extractall(folder_path)
        
download_dataset()

You can see a brief description of each file in the dataset by looking at the README file

In [3]:
##### Read the README file 
!cat ./datasets/README
#####

Files in this directory with sizes:
          0 Jun 19 21:01 README

    2187734 Jun 19 20:55 cacm.all              text of documents
        626 Jun 19 20:58 cite.info             key to citation info
                                                (the X sections in cacm.all)
       2668 Jun 19 20:55 common_words           stop words used by smart
       2194 Jun 19 20:55 make_coll*             shell script to make collection
       1557 Jun 19 20:55 make_coll_term*        ditto (both useless without
                                                smart system)
       9948 Jun 19 20:55 qrels.text             relation giving
                                                    qid did 0 0
                                                to indicate dument did is
                                                relevant to query qid
      13689 Jun 19 20:55 query.text             Original text of the query


----
We are interested in 4 files:
- `cacm.all` : Contains the text for all documents. Note that some documents do not have abstracts available. 
- `query.text` : The text of all queries
- `qrels.text` : The relevance judgements
- `common_words` : A list of common words. This may be used as a collection of stopwords

In [4]:
##### The first 45 lines of the CACM dataset forms the first record
# We are interested only in 3 fields. 
# 1. the '.I' field, which is the document id
# 2. the '.T' field (the title) and
# 3. the '.W' field (the abstract, which may be absent)
!head -45 ./datasets/cacm.all
#####

.I 1
.T
Preliminary Report-International Algebraic Language
.B
CACM December, 1958
.A
Perlis, A. J.
Samelson,K.
.N
CA581203 JB March 22, 1978  8:28 PM
.X
100	5	1
123	5	1
164	5	1
1	5	1
1	5	1
1	5	1
205	5	1
210	5	1
214	5	1
1982	5	1
398	5	1
642	5	1
669	5	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
1	6	1
165	6	1
196	6	1
196	6	1
1273	6	1
1883	6	1
324	6	1
43	6	1
53	6	1
91	6	1
410	6	1
3184	6	1


---

Now, write a function to read in the `cacm.all` file. Note that each document has a variable number of lines. The `.I` field denotes a new document

In [11]:
# TODO: Implement this! (4 points)
def read_cacm_docs(root_folder = "./datasets/"):
    """
        Reads in the CACM documents. The dataset is assumed to be in the folder "./datasets/cacm" be default
        Returns: A list of 2-tuples: (doc_id, document), where 'document' is a single string created by 
            appending the title and abstract (seperated by a "\n"). 
            In case the record doesn't have an abstract, the document is composed only by the title
    """
    
    doc = open(root_folder + 'cacm.all', 'r')
    docs = doc.readlines()
    docs_dict = {}
    id_list = []
    counter =0
    counter_2 =0
    for i in range(len(docs)):
        if docs[i][:2] =='.I':
            id_list.append(docs[i].split(' ')[1][:-1])
            docs_dict[id_list[counter]]=[docs[i+2][:-1]]
            counter += 1

        elif docs[i][:2] =='.W':
            counter_2=2
            key = id_list[counter-1]
            docs_dict[key].append(docs[i+1][:-1])
            while not docs[i+counter_2][1].isupper():
                docs_dict[key].append(docs[i+counter_2][:-1])
                counter_2+=1
#             print(docs[i+counter_2])
                
#             print(docs[i+1],key)
            
            
#         elif line[:2]=='.T':
#             key = id_list[counter]
#             docs[key].append(doc[i+1])
#             counter += 1
#     print(doc.readlines())
    
#     print(docs_dict)
    return docs_dict

docs = read_cacm_docs()

In [10]:
docs['20']

['Accelerating Convergence of Iterative Processes',
 'A technique is discussed which, when applied',
 'A technique is discussed which, when applied',
 'to an iterative procedure for the solution of',
 'an equation, accelerates the rate of convergence if',
 'the iteration converges and induces convergence if',
 'the iteration diverges.  An illustrative example is given.']

In [46]:
root_folder = "./datasets/"
doc = open(root_folder + 'cacm.all', 'r')
# for i, line in enumerate(doc):
#     if line[:2]=='.W':
#         print(i,line)
        
for i, line in enumerate(doc):
    print(i, line)
# doc2[0]


0 .I 1

1 .T

2 Preliminary Report-International Algebraic Language

3 .B

4 CACM December, 1958

5 .A

6 Perlis, A. J.

7 Samelson,K.

8 .N

9 CA581203 JB March 22, 1978  8:28 PM

10 .X

11 100	5	1

12 123	5	1

13 164	5	1

14 1	5	1

15 1	5	1

16 1	5	1

17 205	5	1

18 210	5	1

19 214	5	1

20 1982	5	1

21 398	5	1

22 642	5	1

23 669	5	1

24 1	6	1

25 1	6	1

26 1	6	1

27 1	6	1

28 1	6	1

29 1	6	1

30 1	6	1

31 1	6	1

32 1	6	1

33 1	6	1

34 165	6	1

35 196	6	1

36 196	6	1

37 1273	6	1

38 1883	6	1

39 324	6	1

40 43	6	1

41 53	6	1

42 91	6	1

43 410	6	1

44 3184	6	1

45 .I 2

46 .T

47 Extraction of Roots by Repeated Subtractions for Digital Computers

48 .B

49 CACM December, 1958

50 .A

51 Sugai, I.

52 .N

53 CA581202 JB March 22, 1978  8:29 PM

54 .X

55 2	5	2

56 2	5	2

57 2	5	2

58 .I 3

59 .T

60 Techniques Department on Matrix Program Schemes

61 .B

62 CACM December, 1958

63 .A

64 Friedman, M. D.

65 .N

66 CA581201 JB March 22, 1978  8:30 PM

67 .X

68 3	5	3

69 3	5	3

70 3	5

665 .W

666 The binary number system offers many advantages

667 over a decimal representation for a high-performance, 

668 general-purpose computer.  The greater simplicity of

669 a binary arithmetic unit and the greater compactness 

670 of binary numbers both contribute directly to arithmetic

671 speed.  Less obvious and perhaps more important 

672 is the way binary addressing and instruction formats can

673 increase the overall performance.  Binary addresses 

674 are also essential to certain powerful operations which

675 are not practical with decimal instruction formats. 

676  On the other hand, decimal numbers are essential for

677 communicating between man and the computer.  In 

678 applications requiring the processing of a large volume

679 of inherently decimal input and output data, 

680 the time for decimal-binary conversion needed by a purely

681 binary computer may be significant.  A slower 

682 decimal adder may take less time than a fast binary adder

683 

1165 67	6	67

1166 .I 68

1167 .T

1168 The Role of the University in Computers,

1169 Data Processing and Related Fields

1170 .W

1171 A study was made of university programs in

1172 the United States in the fields of computers, data 

1173 processing, operations research, and other closely related

1174 fields.  University policies, organization, 

1175 administration, faculties, students, researches, curricula,

1176 equipment, and financing were investigated. 

1177  An integrated university program is recommended reflecting

1178 the conviction that many present activities 

1179 related to computers will develop into disciplines and

1180 as such are the legitimate province of the university 

1181 scholar.  Details on a recommended Graduate

1182 School of "Computer Sciences" are given.

1183 .B

1184 CACM September, 1959

1185 .A

1186 Fein, L.

1187 .N

1188 CA590901 JB March 22, 1978  6:05 PM

1189 .X

1190 1205	5	68

1191 68	5	68

1192 68	5	68

1193 68	5	68

1194 1100	6	68


1814 Green, J.

1815 .N

1816 CA590202 JB March 22, 1978  8:22 PM

1817 .X

1818 99	5	99

1819 99	5	99

1820 99	5	99

1821 .I 100

1822 .T

1823 Recursive Subscripting Compilers and List-Types Memories

1824 .B

1825 CACM February, 1959

1826 .A

1827 Carr III, J. W.

1828 .N

1829 CA590201 JB March 22, 1978  8:23 PM

1830 .X

1831 205	4	100

1832 210	4	100

1833 214	4	100

1834 1982	4	100

1835 398	4	100

1836 642	4	100

1837 669	4	100

1838 100	4	100

1839 123	4	100

1840 164	4	100

1841 100	5	100

1842 100	5	100

1843 100	5	100

1844 1	5	100

1845 364	5	100

1846 100	6	100

1847 224	6	100

1848 44	6	100

1849 77	6	100

1850 98	6	100

1851 .I 101

1852 .T

1853 Nuclear Reactor Codes

1854 .B

1855 CACM January, 1959

1856 .A

1857 Nather, V.

1858 Sangren, W.

1859 .N

1860 CA590101 JB March 22, 1978  8:24 PM

1861 .X

1862 101	5	101

1863 101	5	101

1864 101	5	101

1865 .I 102

1866 .T

1867 A Comparison of 650 Programming Methods

1868 .B

1869 CACM December, 1960

1870 .A

1871 C


2270 Holt, A.

2271 .N

2272 CA601114 JB March 20, 1978  6:58 PM

2273 .X

2274 121	4	121

2275 121	5	121

2276 121	5	121

2277 121	5	121

2278 221	5	121

2279 .I 122

2280 .T

2281 Least Squares Fitting of a Great Circle Through Points on a Sphere

2282 .B

2283 CACM November,1960

2284 .A

2285 DeWitte, L.

2286 .N

2287 CA601113 JB March 20, 1978  6:59 PM

2288 .X

2289 122	5	122

2290 122	5	122

2291 122	5	122

2292 297	5	122

2293 122	6	122

2294 .I 123

2295 .T

2296 Compilation for Two Computers with NELIAC

2297 .W

2298 NELIAC, a compiler based on ALGOL, was developed

2299 at the U.S. Navy Electronics Laboratory, San 

2300 Diego,California, as a"boot-strap" compiler for the Remington

2301 Rand Univac COUNTESS computer. This compiler 

2302 was used to generate a version of itself which, running

2303 as a COUNTESS program, generated machine code 

2304 for the Control Data Corporation CDC-1604.  All three

2305 versions of NELIAC accepted essentially identical 

2306 input

...

105672 assessed with a sample of 215 under-graduate business administration

105673 majors.  Cobol proficiency was measured by a final examination

105674 testing (a) knowledge of language rules, (b) ability to read

105675 and debug a program, and (c) the ability to write a program.  Analysis

105676 of multiple covariance was used to statistically adjust test

105677 scores for age and conditional reasoning scores. The findings provide

105678 empirical support for incorporating structured walk-throughs

105679 into the programming learning process more effectively

105680 develop student proficiency in writing Cobol programs.

105681 .B

105682 CACM June, 1979

105683 .A

105684 Lemos, R.S.

105685 .K

105686 Structured walk-throughs, Cobol programming, teaching

105687 of programming, testing programming proficiency

105688 .C

105689 3.51 1.52 2.42 4.22

105690 .N

105691 CA790601 DH August 21, 1979 3:19 PM

105692 .X

105693 3145	4	3145

105694 2887	5	3145

105695 3145	5	3145

10

106202 public-key encryption device and hardware keys.  Each user is responsible 

106203 for his own security and need not rely on the security of

106204 the central facility or the communication links.  A user can safely

106205 store confidential files in the central facility or transmit confidential 

106206 data to other users on the network. 

106207 .B

106208 CACM August, 1979

106209 .A

106210 Denning, D.E.

106211 .K

106212 Personal computing, security, privacy, networks, public-key encryption

106213 .C

106214 2.12 6.20

106215 .N

106216 CA790804 DB January 14, 1980  9:26 AM

106217 .X

106218 2840	4	3158

106219 2869	4	3158

106220 3021	4	3158

106221 3128	4	3158

106222 3158	4	3158

106223 3158	4	3158

106224 3158	4	3158

106225 2436	5	3158

106226 3038	5	3158

106227 3111	5	3158

106228 3158	5	3158

106229 3158	5	3158

106230 3158	5	3158

106231 .I 3159

106232 .T

106233 Further Remark on Stably Updating Mean and Standard Deviation Estimates

106234 .B

106235 CACM 

106740 of the alphabet has one fixed substitute, and the word divisions 

106741 do not change.  In this paper the problem of breaking substitution

106742 ciphers is represented as a probabilistic labeling problem.

106743 Every code letter is assigned probabilities of representing plain text

106744 letters.  These probabilities are updated in parallel for all

106745 code letters, using joint letter probabilities.  Iterating the updating

106746 scheme results in improved estimates that finally lead to

106747 breaking the cipher.  The method is applies successfully to two examples.

106748 .B

106749 CACM November, 1979

106750 .A

106751 Peleg, S.

106752 Rosenfeld, A.

106753 .K

106754 Cryptography, substitution ciphers,

106755 probabilistic classification, relaxation

106756 .C

106757 3.42 3.63

106758 .N

106759 CA791103 DB January 23, 1980  11:15 AM

106760 .X

106761 3175	5	3175

106762 3175	5	3175

106763 3175	5	3175

106764 .I 3176

106765 .T

106766 Storing a Sparse Tab


107424 1919	5	3187

107425 2679	5	3187

107426 3187	5	3187

107427 3187	5	3187

107428 3187	5	3187

107429 864	6	3187

107430 970	6	3187

107431 1175	6	3187

107432 1175	6	3187

107433 1190	6	3187

107434 1228	6	3187

107435 1969	6	3187

107436 1997	6	3187

107437 308	6	3187

107438 308	6	3187

107439 309	6	3187

107440 2042	6	3187

107441 74	6	3187

107442 3187	6	3187

107443 3187	6	3187

107444 507	6	3187

107445 716	6	3187

107446 783	6	3187

107447 .I 3188

107448 .T

107449    Semiotics and Programming Languages

107450 .W

107451    I have based my paper on semiotics and its three dimension. I should insert

107452 at this point that language has many aspects and that pragmatics, semantics and

107453 syntactics do not necessary cover all of them. One can, however, project most 

107454 aspects into the three semiotic dimension and there seems to be a strong 

107455 tendency to do so today.

107456 .B

107457 CACM March, 1966

107458 .A

107459 Zemanek, H.

107460 .N

107461 CA

108044 .B

108045 CACM August, 1966

108046 .A

108047 Korsvold, K.

108048 .N

108049 CA660818 ES March 17, 1982 10:10 AM

108050 .X

108051 1396	5	3204

108052 3204	5	3204

108053 3204	5	3204

108054 3204	5	3204

108055 964	6	3204

108056 1028	6	3204

108057 1029	6	3204

108058 1083	6	3204

108059 1132	6	3204

108060 1214	6	3204

108061 1278	6	3204

108062 1334	6	3204

108063 1365	6	3204

108064 1386	6	3204

108065 1387	6	3204

108066 1388	6	3204

108067 1392	6	3204

108068 1393	6	3204

108069 1394	6	3204

108070 1395	6	3204

108071 1396	6	3204

108072 1397	6	3204

108073 1496	6	3204

108074 284	6	3204

108075 407	6	3204

108076 3199	6	3204

108077 3200	6	3204

108078 3201	6	3204

108079 3202	6	3204

108080 3203	6	3204

108081 3204	6	3204

108082 561	6	3204

108083 730	6	3204



In [ ]:
##### 
assert len(docs) == 3204, "There should be exactly 3024 documents"
##### 

---

Next, let us read the queries. They are formatted similarly: 

In [ ]:
##### The first 15 lines of 'query.text' has 2 queries
# We are interested only in 2 fields. 
# 1. the '.I' - the query id
# 2. the '.W' - the query
# 3. the '.W' field (the abstract, which may be absent)
!head -15 ./datasets/query.text
#####

---

Now, write a function to read in this file:

In [ ]:
# TODO: Implement this! (3 points)
def read_queries(root_folder = "./datasets/"):
    """
        Reads in the CACM queries. The dataset is assumed to be in the folder "./datasets/" be default
        Returns: A list of 2-tuples: (query_id, query)
    """
    
    raise NotImplementedError()
queries = read_queries()

In [ ]:
##### 
assert len(queries) == 64 and all([q[1] is not None for q in queries]), "There should be exactly 64 queries"
##### 

---

Read in the stop words:

In [ ]:
!head ./datasets/common_words

In [ ]:
# TODO: Implement this! (3 points)
def load_stopwords(root_folder = "./datasets"):
    """
    Load the stopwords
    Output: A set of stopwords
    """
    raise NotImplementedError()

stopwords = load_stopwords()
assert len(stopwords) == 428

--- 

We can now write some basic text processing functions. A first step is to tokenize the text. You may use any tokenizer available in the `nltk` library:

In [ ]:
# TODO: Implement this! (5 points)
def tokenize(text):
    """
        Tokenize the text. 
        Input: text - a string
        Output: a list of tokens
    """
    raise NotImplementedError()

In [ ]:
#####
text = "the quick brown fox jumps over the lazy dog"
tokens = tokenize(text)
print(tokens)
#####

---

*Answer the following questions*: 
- Why is stemming necessary, in particular for IR?
    - *TODO: Answer this!*
- Is there any setting (domain, scenario, etc) in which stemming can hurt performance? Illustrate with an example
    - *TODO: Answer this!*

Write a function to stem tokens. Again, you can use the `nltk` library for this

In [ ]:
# TODO: Implement this! (5 points)
def stem_token(token):
    """
        Stem the given token, using any stemmer available from the nltk library
        Input: a single token
        Output: the stem of the token
    """
    raise NotImplementedError()

In [ ]:
####
print([stem_token(t) for t in tokens])
tokens_ = [
    'caresses', 'flies', 'dies', 'mules', 'denied',
    'died', 'agreed', 'owned', 'humbled', 'sized',
    'meeting', 'stating', 'siezing', 'itemization',
    'sensational', 'traditional', 'reference', 'colonizer',
    'plotted']
print([stem_token(t) for t in tokens_])
####

---

*Answer the following questions*: 
- Another processing step (not done here) is to use n-grams. Illustrate why you would want to use n-grams in IR with an example.  
    - *TODO: Answer this!*
- Usage of n-grams exacerbates some problems ex. in bi-gram language models. What is this problem? Suggest one solution 
    - *TODO: Answer this!*

--- 

The following function puts it all together. Given a string, it tokenizes it, and processes it according to the flags that you set.

In [ ]:
#### Putting it all together
def process_text(text, stem=False, remove_stopwords=False, lowercase_text=False):
    
    tokens = []
    for token in tokenize(text):
        if remove_stopwords and token.lower() in stopwords:
            continue
        if stem:
            token = stem_token(token)
        if lowercase_text:
            token = token.lower()
        tokens.append(token)

    return tokens
#### 

Let's create two sets of pre-processed documents

In [ ]:
# In this configuration:
# Don't preprocess the text, except to tokenize 
config_1 = {
  "stem": False,
  "remove_stopwords" : False,
  "lowercase_text": True
} 


# In this configuration:
# Preprocess the text: stem and remove stopwords
config_2 = {
  "stem": True,
  "remove_stopwords" : True,
  "lowercase_text": True, 
} 


We can now process the documents and queries according to the configuration specified above

In [ ]:
####
doc_repr_1 = []
doc_repr_2 = []
for (doc_id, document) in docs:
    doc_repr_1.append((doc_id, process_text(document, **config_1)))
    doc_repr_2.append((doc_id, process_text(document, **config_2)))

####


--- 

## Section 2: Indexing (10 points)


A retrieval function usually takes in a query document pair, and scores a query against a document.  Our document set is quite small - just a few thousand documents. However, consider a web-scale dataset with a few million documents. In such a scenario, it would become infeasible to score every query and document pair. In such a case, we can build an inverted index. From Wikipedia:

> ... , an inverted index (also referred to as a postings file or inverted file) is a database index storing a mapping from content, such as words or numbers, to its locations in a table, .... The purpose of an inverted index is to allow fast full-text searches, at a cost of increased processing when a document is added to the database. ...


Consider a simple inverted index, which maps from word to document. This can improve the performance of a retrieval system significantly. In this assignment, we consider a *simple* inverted index, which maps a word to a set of documents. In practice, however, more complex indices might be used.  


### Building an index

A retrieval function usually takes in a query document pair, and scores a query against a document.  Our document set is quite small - just a few thousand documents. However, consider a web-scale dataset with a few million documents. In such a scenario, it would become infeasible to score every query and document pair. In such a case, we can build an inverted index. From Wikipedia:

> ... , an inverted index (also referred to as a postings file or inverted file) is a database index storing a mapping from content, such as words or numbers, to its locations in a table, .... The purpose of an inverted index is to allow fast full-text searches, at a cost of increased processing when a document is added to the database. ...


Consider a simple inverted index, which maps from word to document. This can improve the performance of a retrieval system significantly. In this assignment, we consider a *simple* inverted index, which maps a word to a set of documents. In practice, however, more complex indices might be used.  


---

In this assignment we will be using an index created in memory, since our dataset is tiny. To get started, build a simple index that maps simply counts the number of tokens present in a document. This index  is built using a python dictionary.

*Answer the following questions*:
- What is the time complexity of retrieving a list of documents from a python `dict` object? 
    - *TODO: Answer this!*
- Consider the case with a 10 million documents. What is the time complexity of retrieval with an inverted index (assuming you can fit the entire index in memory)? (Hint: Consider length of a query $|q|$) 
    - *TODO: Answer this!*
- For a large enough collection, we cannot store an index in memory. How is this tackled in practice (briefly explain)? Comment on the time complexity. 
    - *TODO: Answer this!*
- Mention a use-case in which a simple index (from word -> doc_id) might not suffice anymore. How would you modify the index to suit this use-case (if you can!)  
    - *TODO: Answer this!*
    
    
Now, implement a function to build an index:

In [ ]:
# TODO: Implement this! 10 points
def build_tf_index(documents):
    """
    Build an inverted index (with counts). The output is a dictionary which takes in a token
    and returns a list of (doc_id, count) where 'count' is the count of the 'token' in 'doc_id'
    Input: a list of documents - (doc_id, tokens) 
    Output: An inverted index. [token] -> [(doc_id, token_count)]
    """
    raise NotImplementedError()
 
# Create the 2 indices
tf_index_1 = build_tf_index(doc_repr_1)
tf_index_2 = build_tf_index(doc_repr_2)

# This function returns the correct index 
def get_index(index_set):
    assert index_set in {1, 2}
    return {
        1: tf_index_1,
        2: tf_index_2
    }[index_set]

# This function correctly pre-processes the text given the index set
def preprocess_query(text, index_set):
    assert index_set in {1, 2}
    if index_set == 1:
        return process_text(text, **config_1)
    elif index_set == 2:
        return process_text(text, **config_2)
    

--- 

## Section 3: Retrieval  (80 points)

Now that we have cleaned and processed our dataset, we can start building simple IR systems. 

For now, we consider *simple* IR systems, which involve computing scores from the tokens present in the document/query. More advanced methods are covered in later assignments.

We will implement the following methods in this section:
- TF-IDF
- BM25
- Query Likelihood Models

--- 

### Ranking functions


Probably the simplest IR model is the Bag of Words (BOW) model. Implement a function that scores a query against a document using this model.   

Note that you can use either the count of the token or 'binarize' it i.e set the value equal to 1 if the token appears.   


**Note:** Make sure you use the `get_index` function to retrieve the correct index, and call `preprocess_query` with the correct index!

In [ ]:
# TODO: Implement this! 10 points
def bow_search(query, index_set):
    """
        Perform a search over all documents with the given query. 
        Note #1: You have to use the `get_index` function created in the previous cells
        Note #2: You can binarize the counts if you wish to
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

*Answer the following questions*: 
- The BOW model is might not be a good choice for use in IR. Why? 
    - *TODO: Answer this!*

In [ ]:
####
docs_by_id = dict(docs)
def print_results(docs, len_limit=50):    
    for i, (doc_id, score) in enumerate(docs):
        doc_content = docs_by_id[doc_id].strip().replace("\n", "\\n")[:len_limit] + "..."
        print(f"Rank {i}({score:.2}): {doc_content}")

test_bow = bow_search("report", index_set=1)[:5]
print(f"BOW Results:")
print_results(test_bow)
#### 

Before we implement the tf-idf scoring functions, let's first write a function to compute the document frequencies of all words.  

In [ ]:
# TODO: Implement this! (5 points)
def compute_df(documents):
    """
        Compute the document frequency of all terms in the vocabulary
        Input: A list of documents
        Output: A dictionary with {token: document frequency)
    """
    raise NotImplementedError()



# get the document frequencies of each document
df_1 = compute_df([d[1] for d in doc_repr_1])
df_2 = compute_df([d[1] for d in doc_repr_2])

def get_df(index_set):
    assert index_set in {1, 2}
    return {
        1: df_1,
        2: df_2
    }[index_set]

Next, implement a function that computes a tf-idf score given a query.      

In [ ]:
# TODO: Implement this! 10 points
def tfidf_search(query, index_set):
    """
        Perform a search over all documents with the given query using tf-idf. 
        Note #1: You have to use the `get_index` (and the `get_df`) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

In [ ]:
####
test_tfidf = tfidf_search("report", index_set=1)[:5]
print(f"TFIDF Results:")
print_results(test_tfidf)
####

*Answer the following questions*: 
- It is generally not advisable to use the naive version of tf-idf. Why?
    - *TODO: Answer this!*
- Illustrate with an example why using a sublinear scaling for TF is preferable in some cases.  
    - *TODO: Answer this!*

--- 

*Answer the following questions*: 
- An alternative way to compute a query<>document score is to vectorize both the query and document (where each dimension corresponds to a token), and compute a score. The score can be computed using a dot product between the query and the document vectors. Why is the cosine similary function a better choice, particularly in IR? 
    - *TODO: Answer this!*
- What is the time complexity of a search if we are using the vector space method mentioned in the previous question? What is the time complexity if we're using an index (assume that it fits in memory)? Assume $N$ is the number of documents and $|q|$ is the length of a query. 
    - *TODO: Answer this!*

--- 

#### Query Likelihood Models

In this section you will implement a simple query likelihood model. 

First, let use implement a naive version of a QL model, assuming a multinomial unigram language model (with a uniform prior over the documents). 

**Note:** Make sure you use the `get_index` function to retrieve the correct index, and call `preprocess_query` with the correct index!

--- 

*Answer the following questions*: 
- Write down the formula for computing the query likelihood, assuming a multinomial unigram language model. 
    - *TODO: Answer this!*
- What problem does this naive method have? Suggest a simple way to fix it.
    - *TODO: Answer this!*

In [ ]:
####
def doc_lengths(documents):
    doc_lengths = {doc_id:len(doc) for (doc_id, doc) in documents}
    return doc_lengths

doc_lengths_1 = doc_lengths(doc_repr_1)
doc_lengths_2 = doc_lengths(doc_repr_2)

def get_doc_lengths(index_set):
    assert index_set in {1, 2}
    return {
        1: doc_lengths_1,
        2: doc_lengths_2
    }[index_set]
####

In [ ]:

# TODO: Implement this! 15 points
def naive_ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a naive QL model. 
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

In [ ]:
####
test_naiveql = naive_ql_search("report", index_set=1)[:5]
print(f"TFIDF Results:")
print_results(test_naiveql)
####

Now, let's implement a (slightly more) complex QL model. This model should 'fix' the issue with the previous method. If your model requires hyperparameters, set a reasonable value. 

In [ ]:
# TODO: Implement this! 20 points
def ql_search(query, index_set):
    """
        Perform a search over all documents with the given query using a appropriate QL model. 
        Note #1: You have to use the `get_index` (and get_doc_lengths) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    raise NotImplementedError()

In [ ]:
#### Test the QL model
test_ql_results = ql_search("report", index_set=1)[:5]
print_results(test_ql_results)
print()
test_ql_results_long = ql_search("report " * 10, index_set=1)[:5]
print_results(test_ql_results_long)
####

*Answer the following questions*: 
- What happens to the query likelihood for long queries? What is a simple fix for this issue?
    - *TODO: Answer this!*


--- 

#### BM25

In this section, we will implement the widely used and hard to beat BM25 scoring function. 


In [ ]:
# TODO: Implement this! (20 points)
def bm25_search(query, index_set):
    """
        Perform a search over all documents with the given query using BM25. 
        Note #1: You have to use the `get_index` (and `get_doc_lengths`) function created in the previous cells
        Note #2: You might have to create some variables beforehand and use them in this function
        Input: 
            query - a (unprocessed) query
            index_set - the index to use
        Output: a list of (document_id, score), sorted in descending relevance to the given query 
    """
    
    raise NotImplementedError()

In [ ]:
#### Test the BM25 model
test_bm25_results = bm25_search("report", index_set=1)[:5]
print_results(test_bm25_results)
####



*Answer the following questions*: 
- Briefly explain how the BM25 model improves upon the tf-idf model.
    - *TODO: Answer this!*
    
---

In [ ]:
#### Highlighter function
# class for results
ResultRow = namedtuple("ResultRow", ["doc_id", "snippet", "score"])
# doc_id -> doc
docs_by_id = dict((d[0], d[1]) for d in docs)

def highlight_text(document, query, tol=17):
    import re
    tokens = tokenize(query)
    regex = "|".join(f"(\\b{t}\\b)" for t in tokens)
    regex = re.compile(regex, flags=re.IGNORECASE)
    output = ""
    i = 0
    for m in regex.finditer(document):
        start_idx = max(0, m.start() - tol)
        end_idx = min(len(document), m.end() + tol)
        output += "".join(["...",
                        document[start_idx:m.start()],
                        "<strong>",
                        document[m.start():m.end()],
                        "</strong>",
                        document[m.end():end_idx],
                        "..."])
    return output.replace("\n", " ")


def make_results(query, search_fn, index_set):
    results = []
    for doc_id, score in search_fn(query, index_set):
        highlight = highlight_text(docs_by_id[doc_id], query)
        if len(highlight.strip()) == 0:
            highlight = docs_by_id[doc_id]
        results.append(ResultRow(doc_id, highlight, score))
    return results
####

---
---

The widget below allows you to play with the search functions you've written so far. This can be used, for example, to answer some of the theory questions

In [ ]:
# Set this to the function you want to test
# this function should take in a query (string)
# and return a sorted list of (doc_id, score) 
# with the most relevant document in the first position
search_fn = bm25_search
index_set = 1

text = widgets.Text(description="Search Bar", width=200)
display(text)

def handle_submit(sender):
    print(f"Searching for: '{sender.value}'")
    
    results = make_results(sender.value, search_fn, index_set)
    
    # display only the top 5
    results = results[:5]
    
    body = ""
    for idx, r in enumerate(results):
        body += f"<li>Document #{r.doc_id}({r.score}): {r.snippet}</li>"
    display(HTML(f"<ul>{body}</ul>"))
    

text.on_submit(handle_submit)

## Section 4: Offline Evaluation (45 points)

Before we jump in and implement an algorithm for retrieval, we first have to learn how to evaluate such a system. In particular, we will work with offline evaluation metrics. These metrics are computed on a dataset with known relevance judgements.

Implement the following evaluation metrics. 

1. Precision
2. Recall
3. Mean Average Precision
4. Expected Reciprocal Rank

---
*Answer the following questions*: 
- What are the main limitations of an offline evaluation?
    - *TODO: Answer this!*

---

Let's take a look at the `qrels.text` file, which contains the ground truth relevance scores. The relevance labels for CACM are binary - either 0 or 1. 


In [ ]:
!head ./datasets/qrels.text

The first column is the `query_id` and the second column is the `document_id`. You can safely ignore the 3rd and 4th columns. Write a function to read in the file: 

In [ ]:
# TODO: Implement this!
def read_qrels(root_folder = "./datasets/"):
    """
        Reads the qrels.text file. 
        Output: A dictionary: query_id -> [list of relevant documents]
    """
    raise NotImplementedError()

qrels = read_qrels()

In [ ]:
####
assert len(qrels) == 52, "There should be 52 queries with relevance judgements"
assert sum(len(j) for j in qrels.values()) == 796, "There should be a total of 796 Relevance Judgements"
####

Now, implement the metrics below. 

**Note:** For a given query `query_id`, you can assume that documents *not* in `qrels[query_id]` are not relevant to `query_id`. 


In [ ]:
# TODO: Implement this! (10 points)
def recall_k(results, relevant_docs, k):
    """
        Compute Recall@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Recall@K
    """
    raise NotImplementedError()
    
# TODO: Implement this! (10 points)
def precision_k(results, relevant_docs, k):
    """
        Compute Precision@K
        Input: 
            results: A sorted list of 2-tuples (document_id, score), 
                    with the most relevant document in the first position
            relevant_docs: A set of relevant documents. 
            k: the cut-off
        Output: Precision@K
    """
    raise NotImplementedError()

# TODO: Implement this! (10 points)
def average_precision(results, relevant_docs):
    """
        Compute Average Precision (for a single query - the results are 
        averaged across queries to get MAP in the next few cells)
        Hint: You can use the recall_k and precision_k functions here!
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: Average Precision
    """
    raise NotImplementedError()


# TODO: Implement this! (15 points)
def err(results, relevant_docs):
    """
        Compute the expected reciprocal rank.
        Hint: https://dl.acm.org/doi/pdf/10.1145/1645953.1646033?download=true
        Input: 
            results: A sorted list of 2-tuples (document_id, score), with the most 
                    relevant document in the first position
            relevant_docs: A set of relevant documents. 
        Output: ERR
        
    """
    raise NotImplementedError()
####

*Answer the following questions*: 
- What are the main drawbacks of precision & recall?
    - *TODO: Answer this!*
- What problems with Precision@K does Average Precision solve? 
    - *TODO: Answer this!*
- The CACM dataset has *binary* relevance judgements. However, a more suitable way of assigning judgements is to use graded relevance. Mention a metric which might be more suitable for a graded relevance, and breifly explain why. 
    - *TODO: Answer this!*
- Consider a text processing step: stemming. What effect does this have on metrics? (Hint: Try changing the pre-processing config and try it out!)
    - *TODO: Answer this!*

---

Let's define some metrics@k using [partial functions](https://docs.python.org/3/library/functools.html#functools.partial)

In [ ]:
####
recall_at_1 = partial(recall_k, k=1)
recall_at_5 = partial(recall_k, k=5)
recall_at_10 = partial(recall_k, k=10)
precision_at_1 = partial(precision_k, k=1)
precision_at_5 = partial(precision_k, k=5)
precision_at_10 = partial(precision_k, k=10)
####

---

The following function evaluates a `search_fn` using the `metric_fn`. Note that the final number is averaged over all the queries

In [ ]:
####
def evaluate_search_fn(search_fn, metric_fn, index_set):
    # build a dict query_id -> query 
    queries_by_id = dict((q[0], q[1]) for q in queries)
    
    metrics = np.zeros(len(qrels), dtype=np.float32)
    for i, (query_id, relevant_docs) in enumerate(qrels.items()):
        query = queries_by_id[query_id]
        results = search_fn(query, index_set)
        metrics[i] = metric_fn(results, relevant_docs)
    
    return metrics.mean()
####

In [ ]:
index_sets = {1, 2}

list_of_metrics = [
    ("ERR", err),
    ("MAP", average_precision),
    ("Recall@1",recall_at_1),
    ("Recall@5", recall_at_5),
    ("Recall@10", recall_at_10),
    ("Precision@1", precision_at_1),
    ("Precision@5", precision_at_5),
    ("Precision@10", precision_at_10)]

list_of_search_fns = [
    ("NaiveQL", ql_search),
    ("QL", ql_search),
    ("BM25", bm25_search),
    ("BOW", bow_search),
    ("TF-IDF", tfidf_search)
]


results = {}
for index_set in index_sets:
    print(f"Index: {index_set}")
    for search_fn_name, search_fn in list_of_search_fns:
        print(f"\tEvaluating Search Function: {search_fn_name}")
        results[search_fn_name] = {}
        for metric_name, metric_fn in list_of_metrics:
            r = evaluate_search_fn(search_fn, metric_fn, index_set).mean()
            print(f"\t\tMetric: {metric_name}: {r}")
            results[search_fn_name][metric_name] = r
        print()

## Section 5: Results and Analysis (20 points)

The `results` dictionary contains the results for all search functions we implemented. Plot the results in bar charts, with clear labels:

In [ ]:
# TODO: Implement this! (20 points)

Write a summary of what you observe in the results.
You summary should compare results across the 2 indices and the methods being used. State what you expected to see in the results, followed by either supporting evidence *or* justify why the results did not support your expectations.      
*Hint*: You may build upon the answers from the previous sections. 

*TODO: Answer this!*